In [1]:
!git clone https://github.com/mueedurrehman/distiller.git
%cd distiller
!pip3 install -e .

Cloning into 'distiller'...
remote: Enumerating objects: 11, done.
remote: Counting objects: 100% (11/11), done.
remote: Compressing objects: 100% (7/7), done.
remote: Total 6174 (delta 4), reused 6 (delta 4), pack-reused 6163
Receiving objects: 100% (6174/6174), 39.83 MiB | 31.86 MiB/s, done.
Resolving deltas: 100% (4327/4327), done.
/content/distiller
Obtaining file:///content/distiller
     |████████████████████████████████| 2.1MB 13.3MB/s 
     |████████████████████████████████| 734.6MB 25kB/s 
     |████████████████████████████████| 10.2MB 84kB/s 
     |████████████████████████████████| 460kB 50.3MB/s 
     |████████████████████████████████| 110.5MB 46kB/s 
     |████████████████████████████████| 51kB 9.3MB/s 
     |████████████████████████████████| 798kB 43.3MB/s 
     |████████████████████████████████| 112kB 55.0MB/s 
     |████████████████████████████████| 1.7MB 45.7MB/s 
     |████████████████████████████████| 235kB 60.7MB/s 
     |████████████████████████████████| 153kB 56.4M

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
import torch
import torchvision
import torchvision.transforms as transforms
import torchvision.models as models
from torchsummary import summary
import matplotlib.pyplot as plt
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import time
import math
import yaml
import distiller
from collections import OrderedDict
import os
import pandas as pd

In [3]:
!cp "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/OneShotElementBaseNoOptResults/92.49-82.6/best.pth.tar" .
# !cp ../../../drive/MyDrive/CS6787\ -\ Final\ Project/Google\ Colab\ Scripts/Quantization\ Models/Resnet56\ Quantization\ Stats/resnet56_quant_stats.yaml .

OneShotElementBaseNoOptResults/92.49-82.6

92.49
82.6

In [4]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Symmetric/4bitSymmetricQA.yaml" ./data --resume="best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QASparseResults" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 | 21.69580 |  48.07030 |   48.07030 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             62 |    0.00000 |    0.00000 |  0.00000 |  3.12500 |  3.12500 |    3.12500 |  2.18030 |  -7.23438 |    7.23438 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |  0.03215 |  -0.00030 |    0.00955 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |           3672 |    0.00000 |    0.00000 |  7.81250 | 56.68945 |  0.00000 |   90.03906 |  0.03223 |  -0.00030 |    0.00955 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 1, 1)  |            64 |

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Symmetric/6bitSymmetricQA.yaml" ./data --resume="best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QASparseResults" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  91.60326 | 201.94902 |  201.94902 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             62 |    0.00000 |    0.00000 |  0.00000 |  3.12500 |  3.12500 |    3.12500 |   8.99326 | -30.29688 |   30.29688 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |   0.03215 |  -0.00030 |    0.00955 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |           3685 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   90.00380 |   0.03215 |  -0.00030 |    0.00955 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 1, 1)  |            

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Symmetric/8bitSymmetricQA.yaml" ./data --resume="best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QASparseResults" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  371.10596 |  817.36835 |  817.36835 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             62 |    0.00000 |    0.00000 |  0.00000 |  3.12500 |  3.12500 |    3.12500 |   36.47074 | -122.60938 |  122.60938 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |    0.03215 |   -0.00030 |    0.00955 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |    0.03215 |   -0.00030 |    0.00955 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 1, 1)  |    

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Symmetric/10bitSymmetricQA.yaml" ./data --resume="best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QASparseResults" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  5961.14062 | 13125.55566 | 13125.55566 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             62 |    0.00000 |    0.00000 |  0.00000 |  3.12500 |  3.12500 |    3.12500 |   585.41754 | -1969.37500 |  1969.37500 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |     0.03215 |    -0.00030 |     0.00955 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |     0.03215 |    -0.00030 |     0.00955 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Symmetric/12bitSymmetricQA.yaml" ./data --resume="best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QASparseResults" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  5959.21484 | 13124.94727 | 13124.94727 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             62 |    0.00000 |    0.00000 |  0.00000 |  3.12500 |  3.12500 |    3.12500 |   585.41040 | -1969.23438 |  1969.23438 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |     0.03215 |    -0.00030 |     0.00955 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |     0.03215 |    -0.00030 |     0.00955 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Symmetric/14bitSymmetricQA.yaml" ./data --resume="best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QASparseResults" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 | 23847.79688 |  52510.11328 |  52510.11328 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             62 |    0.00000 |    0.00000 |  0.00000 |  3.12500 |  3.12500 |    3.12500 |  2342.09766 |  -7878.70312 |   7878.70312 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |     0.03215 |     -0.00030 |      0.00955 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |           3687 |    0.00000 |    0.00000 |  7.81250 | 56.64062 |  0.00000 |   89.99837 |     0.03215 |     -0.00030 |      0.00955 |
| 174 | module.layer3.2.conv1.weight_scale             | 

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Symmetric/16bitSymmetricQA.yaml" ./data --resume="best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QASparseResults" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=avg --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy